In [1]:
import os
import json
import dreem
import numpy as np
import pandas as pd

import plotly.graph_objects as go

In [112]:
## Plot and save coverage and dms signal for all references

samples_dir = '/Users/alberic/Desktop/Pro/RouskinLab/projects/deep_learning/RNA_data_old/DMS/dataset/Justin/samples/'

# Create a study object to process the data
study = dreem.draw.study.Study(
    data = [json.load(open(os.path.join(samples_dir,'Dragui_1_S6_L001/output/Dragui_1_S6_L001.json'), 'r')),
            json.load(open(os.path.join(samples_dir,'Dragui_2_S7_L001/output/Dragui_2_S7_L001.json'), 'r'))]
)

samples = study.df['sample'].unique() # First one is untreated, second and third one are treated

for sample in samples:
    for ref in study.get_df(sample=sample)['reference'].unique():

        # Base coverage
        save_dir = os.path.join(samples_dir, sample, 'plots', ref)
        if not os.path.exists(save_dir):
            os.makedirs(save_dir)
        result = study.base_coverage(sample=sample, reference=ref)
        result['fig'].write_image(os.path.join(save_dir, 'base_coverage.png'))

        # Mutation fraction
        result = study.mutation_fraction(sample=sample, reference=ref)
        result['fig'].update_layout(xaxis = dict(tickmode = 'array', tickvals=[]))
        result['fig'].write_image(os.path.join(save_dir, 'mutation_fraction.png'))


# Filter out references with nan in sub_rate
study.df = study.df[study.df['min_cov']>0].reset_index(drop=True)

df_treated = study.df[study.df['sample']!=samples[0]]
df_untreated = study.df[study.df['sample']==samples[0]]

Turning data into a dataframe...
Dragui_1_S6_L001... Dragui_2_S7_L001... Done.
Setting dataframe...
Done.


In [31]:
treated_signals = np.concatenate(df_treated.sub_rate.tolist())
untreated_signals = np.concatenate(df_untreated.sub_rate.tolist())

threshold_dms = 0.2

fig = go.Figure()
fig.add_trace(go.Histogram(x=treated_signals[treated_signals<threshold_dms], name='Treated'))
fig.add_trace(go.Histogram(x=untreated_signals[untreated_signals<threshold_dms], name='Untreated'))
fig.update_layout(barmode='overlay', title=f'DMS reactivities between treated and untreated samples (capped at {threshold_dms})', xaxis_title='DMS reactivity', yaxis_title='Probability')
fig.update_traces(opacity=0.75)
fig.show()

In [32]:
## Plot histogram of DMS for A/C and G/U separately

AC_dms = []
GU_dms = []



for i, row in df_treated.iterrows():
    AC_mask = np.where(np.isin(list(row.sequence), ['A', 'C']), True, False)

    AC_dms += list(np.array(row.sub_rate)[AC_mask])
    GU_dms += list(np.array(row.sub_rate)[~AC_mask])

AC_dms = np.array(AC_dms)
GU_dms = np.array(GU_dms)

threshold_dms = 0.2
fig = go.Figure()
fig.add_trace(go.Histogram(x=AC_dms[AC_dms<threshold_dms], name='A/C', histnorm='probability'))
fig.add_trace(go.Histogram(x=GU_dms[GU_dms<threshold_dms], name='G/U', histnorm='probability'))
fig.update_layout(barmode='overlay', title=f'DMS reactivity histogram between bases for treated samples (capped at {threshold_dms})', xaxis_title='DMS reactivity', yaxis_title='Probability')
fig.update_traces(opacity=0.75)
fig.show()


In [113]:
## Bar plot of the minimum coverage across all reference, sorted

fig = go.Figure()

fig.add_trace(go.Bar(
    x=np.arange(len(study.df['min_cov'])),
    y=df_treated['min_cov'].sort_values(ascending=False),
    name='min_cov'
))
fig.update_layout(title=f'Minimum coverage across all references for treated samples', 
                  xaxis_title='Reference number', yaxis_title='Minimum coverage')
fig.update_yaxes(type="log")
fig.show()

In [93]:
## Average coverage and dms signal across all references

streched_dms = []
streched_coverage = []
streched_bases = np.linspace(0, 1000, 1000)

for i, row in df_treated.iterrows():
    streched_dms.append(np.interp(streched_bases, np.arange(len(row['sub_rate'])), row['sub_rate']))
    streched_coverage.append(np.interp(streched_bases, np.arange(len(row['cov'])), row['cov']))

def plot_average_std(signals):

    average_signal = np.mean(signals, axis=0)
    std_signal = 0.3*np.std(signals, axis=0)


    fig = go.Figure()

    # Add the average signal as a bar plot
    fig.add_trace(go.Scatter(
        x=np.arange(len(average_signal)),
        y=average_signal,
    ))

    fig.add_trace(go.Scatter(
        x=np.arange(len(average_signal)),
        y=average_signal - std_signal,
        mode='lines',
        line=dict(color='blue', width=0.5),
        fill=None,
    ))
    fig.add_trace(go.Scatter(
        x=np.arange(len(average_signal)),
        y=average_signal + std_signal,
        mode='lines',
        line=dict(color='blue', width=0.5),
        fill='tonexty'
    ))

    

    # Show the plot
    return fig

In [114]:
fig = plot_average_std(streched_dms)
# Update layout and axis labels
fig.update_layout(
    title='Average Signal with Standard Deviation',
    xaxis_title='Normalized position',
    yaxis_title='DMS signal',
    showlegend=False,
    height=600,
)
fig.show()

In [115]:
fig = plot_average_std(streched_coverage)
# fig.add_trace(go.Scatter(x=np.arange(len(streched_coverage[0])), y=3000*np.ones(len(streched_coverage[0])), mode='lines', line=dict(color='red', width=0.5)))
# Update layout and axis labels
fig.update_layout(
    title='Average Coverage with Standard Deviation',
    xaxis_title='Normalized position',
    yaxis_title='coverage',
    showlegend=False
)
fig.update_yaxes(type="log")
fig.show()

In [25]:
## Analyze replicate signals

if len(samples) == 3:

    pearson = []
    pearson_AC = []

    rmse = []
    rmse_AC = []

    min_cov = []

    for ref in df_treated.reference.unique():

        df1 = study.get_df(sample=samples[1], reference=ref)
        df2 = study.get_df(sample=samples[2], reference=ref)

        assert len(df1) ==1
        assert len(df2) ==1
        assert df1['sequence'].iloc[0] == df2['sequence'].iloc[0]


        dms1 = np.array(df1['sub_rate'].iloc[0])
        dms2 = np.array(df2['sub_rate'].iloc[0])


        pearson.append(np.corrcoef(dms1, dms2)[0,1])
        rmse.append(np.sqrt(np.mean((dms1-dms2)**2)))

        AC_mask = np.where(np.isin(list(df1['sequence'].iloc[0]), ['A', 'C']), True, False)

        pearson_AC.append(np.corrcoef(dms1[AC_mask], dms2[AC_mask])[0,1])
        rmse_AC.append(np.sqrt(np.mean((dms1[AC_mask]-dms2[AC_mask])**2)))

        min_cov.append(np.min([df1['min_cov'].iloc[0], df2['min_cov'].iloc[0]]))
        break

else:
    print('Not enough samples to analyze replicates')

Not enough samples to analyze replicates


## Additional analysis

In [100]:
n_zeros_begin = []

for sub_rate in study.df['sub_rate']:
    n_zero = 0
    for i in range(len(sub_rate)):
        if sub_rate[len(sub_rate)-1-i]==0:
            n_zero += 1
        else:
            break
    n_zeros_begin.append(n_zero)

In [101]:
import plotly.express as px
px.histogram(n_zeros_begin)

## Findings

- Most of the data has good coverage, only 2 ref have 0 coverage in first sample, 3 in second sample
- All ref have the first two bases with 0 dms
- Lower coverage and DMS signal at the end of the sequences
- Untreated sample has lower reactivity than treated sample
- A/C bases have higher reactivity than G/U bases

In [99]:
## Compare with Seismic output

correleation = []
dms1 = []
dms2 = []

out_dir = '/Users/alberic/Downloads/dragui_rerun/out/graph/Dragui_1_S6_L001'

df_tested = df_untreated

for dir in os.listdir(out_dir):
    if dir.startswith('ENSG'):
        try:
            data = pd.read_csv(os.path.join(out_dir, dir, 'full', 'related_serial-m_fraction.csv'))

            dms1 += (data.Mutated.tolist())
            dms2 += (df_tested[df_tested.reference==dir.replace('.', '-')]['sub_rate'].iloc[0])

            assert ''.join(data.Base.tolist()) == df_tested[df_tested.reference==dir.replace('.', '-')]['sequence'].iloc[0]

            correleation.append(np.corrcoef(data.Mutated.tolist(), df_tested[df_tested.reference==dir.replace('.', '-')]['sub_rate'].iloc[0])[0,1])

        except:
            print(dir)

print(np.mean(correleation))

ENSG00000142623.11
ENSG00000139223.4
ENSG00000143107.10
ENSG00000151224.13
ENSG00000147570.10
ENSG00000143816.8
ENSG00000146904.9
ENSG00000144227.5
ENSG00000138316.11
ENSG00000152193.8
ENSG00000145863.11
ENSG00000139610.2
ENSG00000138615.6
ENSG00000148602.6
ENSG00000140836.17
ENSG00000150457.9
0.9810309627555833


In [97]:
print(np.median(correleation))

0.9937664645664867


In [95]:
import plotly.express as px
px.histogram(correleation)

In [80]:
go.Figure(go.Scatter(x=dms1, y=dms2, mode='markers')).show()